# Named Entities Recognition

In [1]:
import os
import nltk
import json
import re
import codecs
import string
import subprocess
import unicodedata
import collections
import pandas as pd


from nltk import ne_chunk
from polyglot.text import Text

from nltk import word_tokenize
from collections import defaultdict
from polyglot.detect import Detector
from nltk.tag import StanfordNERTagger
from nltk.tag import StanfordPOSTagger
from nltk.internals import find_jars_within_path

from polyglot.downloader import downloader
#downloader.download("embeddings2.en","ner2.en")



# Important paths to access data

In [2]:
directory_name = os.path.dirname('/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Afghanistan 0 18Mar2015.txt')
directory_name

'/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt'

In [3]:
sample_file = os.path.join('/home/alice','/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Afghanistan 0 18Mar2015.txt')
sample_file

'/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Afghanistan 0 18Mar2015.txt'

In [4]:
path = ("/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/")
path

'/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/'

In [5]:
# We will work with files in this directory
os.path.basename('/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/')

''

In [6]:
# this can differenciate a directory and a file

os.path.split('/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Afghanistan 0 18Mar2015.txt')

('/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt',
 'Afghanistan 0 18Mar2015.txt')

##  Data storage customization

In [7]:
## Set important paths

BASE = os.path.join(os.path.dirname('/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Afghanistan 0 18Mar2015.txt'))
BASE

'/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt'

In [8]:
DOCS = os.path.join("scraped_data", "files_in_txt")
DOCS

'scraped_data/files_in_txt'

In [9]:
path = BASE
path

'/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt'

In [10]:
# list of files we have.
os.listdir(path)

['Nepal MDRNP008 04Aug2016.txt',
 'Serbia MDRRS012 07Apr2016.txt',
 'Bangladesh MDRBD016 05Aug2016.txt',
 'Timor-Leste MDRTP004 25Oct2016.txt',
 'Ghana MDRGH013 21Nov2016.txt',
 'Niger MDRNE013 30Jun2016.txt',
 'Democratic People Republic of Korea MDRKP007 21Aug2015.txt',
 'Philippines MDRPH019 26Feb2016.txt',
 'Namibia MDRNA009 03May2016.txt',
 'Liberia MDRLR002 13Sep2016.txt',
 'Maldives MAAMV001 29Apr2015.txt',
 'Niger MDRNE013 29May2015.txt',
 'MENA regional office MDR81003 07Aug2015.txt',
 'Cameroon MDRCM018 27May2015.txt',
 'Mongolia MDRMN005 25Oct2016.txt',
 'South Sudan MAASS001 28Apr2015.txt',
 'Papua New Guinea MDRPG005 29Jul2016.txt',
 'Lebanon MDRLB005 12Jan2015.txt',
 'Ethiopia MDRET016 25Jan2016.txt',
 'Bangladesh MDRBD017 25Oct2016.txt',
 'Bolivia MDRBO010 13Mar2015.txt',
 'Rwanda MDRRW011 04Oct2016.txt',
 'Sierra Leone MDRSL005 27Apr2016.txt',
 'Niger MDRNE014 25Aug2015.txt',
 'Chile MDRCL010 04Mar2015.txt',
 'Greece MDRGR001 07Oct2016.txt',
 'Honduras MDRHN008 10Sep201

In [11]:
#To open pdf
#import webbrowser
#webbrowser.open_new(r'file:/home/alice/Documents/Project/info_extraction/scraped_data/scraped_appeals/Belarus MDRBY005 12Jan2015.pdf')

In [12]:
address = os.listdir(path)

In [13]:
len(address)

1260

In [14]:
path

'/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt'

In [15]:
DOCS

'scraped_data/files_in_txt'

# Data description:
### Our target files are in  txt  format .


In [16]:
def get_documents(path=BASE):
    
    '''Total number of txt file we have in corpus folder'''
    
    for name in os.listdir(path):
        if name.startswith('') and name.endswith('.txt'):
            yield os.path.join(path, name)
print(len(list(get_documents())))

1260


# NLTK corpus 

In [17]:
CORPUS = os.path.join(BASE, "", "corpus")

In [18]:
path = "/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/"

In [19]:
## Create a path to extract the corpus.

CORPUS = os.path.join("/home/alice/Documents/Project/info_extraction/scraped_data", "corpus")

In [20]:
#fname = os.path.splitext(os.path.basename("/home/alice/Documents/Project/info_extraction/scraped_data/Malawi MDRMW012 06Dec2016"))[0] + ".txt"
fname =' /home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Afghanistan 0 18Mar2015.txt'

In [21]:
#def extract_corpus(BASE,CORPUS):
#    for path in get_documents(BASE):
#        example_file = '/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Tanzania MDRTZ016 10Mar2015.txt'
#        document = open(example_file, 'r').read()
#        print(len(document))     

In [22]:
# sample file 

example_file = '/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Afghanistan 0 18Mar2015.txt'
print(example_file)

/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Afghanistan 0 18Mar2015.txt


In [23]:
#example_file = '/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Tanzania MDRTZ016 10Mar2015.txt'

In [24]:
'''get the number of strings compose sample file before filtering'''
document = open(example_file, 'r').read()
print(len(document))

9014


In [25]:
'''Remaining string after filtering'''
document = filter(
            lambda char: char in string.printable,
            unicodedata.normalize('NFKD', document)
        )
len(list(document)) #   number of remaining strings after filt

8990

In [26]:
# The filter removed 24 = 9014-8990 special characters 

In [27]:
corpus = '/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/corpus/'

In [28]:
#outpath = os.path.join(corpus, fname)
outpath = '/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/corpus/'


### How to read a single report , remove nonprintable characters by  NRKF unicode and write the fitered report on outpth

In [29]:
## For a sample file

In [30]:
def sample_corpus(BASE,CORPUS):
    #for path in get_documents(BASE):
        example_file = '/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt/Afghanistan 0 18Mar2015.txt'
        document = open(example_file, 'r').read()
        print(len(document))
        document = filter(
            lambda char: char in string.printable,
            unicodedata.normalize('NFKD', document)
        )
        document = ''.join(list(document))
        print(document[:100])
        fname = os.path.basename(example_file)
        print(fname)
        outpath = os.path.join(CORPUS, fname)
        print(outpath)

        with codecs.open(outpath, 'w') as f:
            f.write(document)
    

In [31]:
sample_corpus(BASE, CORPUS)

9014
Information Bulletin n 1
Glide n AV-2015-000016-AFG
18 March 2015
This bulletin is being issued
for 
Afghanistan 0 18Mar2015.txt
/home/alice/Documents/Project/info_extraction/scraped_data/corpus/Afghanistan 0 18Mar2015.txt


#  TOP 25 LINES Filtered corpus

In [32]:
## WHY DID WE CONSIDERED FIRST 25 FIVE LINES ONLY?
#=================================================
#1.##  -For most of the pdf reports from IFRC, there is a "small table" containing important data,  
#2.##  - the txt files gotten    from conversion  of PDF made  that "small table"  into almost  25 first lines of each txt document.
#3.##  -I SPLIT THOSE TOP 25 LINES FOR EACH REPORT I COLLECTED THEM AS NEW CORCUP FOLDER CALLED "initial_lines_txt"

In [33]:

def all_corpus(BASE,CORPUS):
    '''Returns filtered corpus for the whole folder '''

    for path in get_documents(BASE):
        #print(path)
        document = open(path, 'r').read()
        #print(len(document))
        document = filter(
            lambda char: char in string.printable,
            unicodedata.normalize('NFKD', document.encode('utf-8').decode('utf-8'))
        )
        document = ''.join(document)
        document = "\n".join(document.split('\n')[:25])
        fname = os.path.basename(path)
        outpath = os.path.join(
            "/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt", 
            fname)

        with codecs.open(outpath, 'w') as f:
            f.write(document)
    

In [34]:
all_corpus(path,CORPUS)

### Customizable NLTK corpus to access txt data on the disk an load the data

In [35]:
kddcorpus = nltk.corpus.PlaintextCorpusReader(
    "/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt",  
    '.*\.txt')  # For a full text :"/home/alice/Documents/Project/info_extraction/scraped_data/files_in_txt",
kddcorpus

<PlaintextCorpusReader in '/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt'>

In [36]:
# Just a look on top 15 documents

initial_ids = kddcorpus.fileids()[:15]; initial_ids

['- Global - MAA00001 22Jul2015.txt',
 '- Global - MAA00006 24Apr2015.txt',
 '- Global - MAA00010 10Nov2015.txt',
 '- Global - MAA00021 02Jun2015.txt',
 '- Global - MAA00028 01May2015.txt',
 '- Global - MAA00029 21Jun2016.txt',
 '- Global - MAA00040 02Jun2015.txt',
 '- Global - MAA00040 10Nov2015.txt',
 '- Global - MAA00040 12May2015.txt',
 '- Global - MDR00001 01Jun2016.txt',
 '- Global - MDR00001 21Apr2015.txt',
 '- Global - MDR42003 01Jun2016.txt',
 '- Global - MDR42003 02Feb2016.txt',
 '- Global - MDR42003 04Mar2016.txt',
 '- Global - MDR42003 22Jun2016.txt']

### FreqDist to calculate sum of words we have for corpus and stopwords

In [37]:
'''How many words and stopwords in our corpus ? '''

words = nltk.FreqDist(kddcorpus.words())
count = sum(words.values())
vocab = len(words)

print("Corpus contains a vocabulary of {} and a word count of {}.".format(
    count, vocab
))

Corpus contains a vocabulary of 343611 and a word count of 11843.


In [38]:
#sample file on position 29 called 'Africa regional office MDR60002 03Nov2015.txt'

fids = kddcorpus.fileids()[28];fids

'Africa regional office MDR60002 03Nov2015.txt'

# NERC Tools  to the corpus 

#### For this Research we are using starnford model  version 2014  but later we will use 2016 version for comparaison.


In [39]:
'''    
   Download jar and model of stanford of version 2014 from the NLP website
   - Return a disctionary of location, persons, organization and others 
    '''
# root of model, jar and stanford packages.
root  = os.path.expanduser('~/models/stanford-ner-2014-01-04/')
# later We will uroot = os.path.expanduser('~/models/stanford-corenlp-full-2016-10-31/') 


model = os.path.join(root, 'classifiers/english.muc.7class.distsim.crf.ser.gz')


jar  = os.path.join(root, 'stanford-ner-2014-01-04.jar')

# STANFORD NER FOR TOP 25 LINES

In [49]:
def stanford_entities(fileids=None, corpus=kddcorpus):
    
    jar = "/home/alice/models/stanford-ner-2014-01-04/stanford-ner-2014-01-04.jar"
    model = "/home/alice/models/stanford-ner-2014-01-04/classifiers/english.muc.7class.distsim.crf.ser.gz"
    
    results = defaultdict(lambda: defaultdict(list))
    fileids = fileids or corpus.fileids()
    tagger  = StanfordNERTagger(model, jar)

    for fileid in fileids:
        text  = corpus.words(fileid)

        chunk = []

        for token, tag in tagger.tag(text):
            if tag == 'O':
                if chunk:
                    # Flush the current chunk
                    etext =  " ".join([c[0] for c in chunk])
                    etag  = chunk[0][1]
                    chunk = []

                    if etag == 'PERSON':
                        key = 'persons'
                    elif etag == 'ORGANIZATION':
                        key = 'organizations'
                    elif etag == 'LOCATION':
                        key = 'locations'
                    else:
                        key = 'other'

                    results[fileid][key].append(etext)

            else:
                chunk.append((token, tag)) # Build chunk from tags

    return results

In [50]:
stanford_entities(fileids=None, corpus=kddcorpus)

defaultdict(<function __main__.stanford_entities.<locals>.<lambda>>,
            {'Kenya MDRKE018 02Oct2015.txt': defaultdict(list,
                         {'locations': ['Kenya',
                           'Hong Kong',
                           'Kenya',
                           'Japan',
                           'Islamic Relief Kenya',
                           'Dadaab'],
                          'organizations': ['Red Cross Red Crescent Movement',
                           'International Committee of the Red Cross',
                           'Norwegian Red Cross',
                           'British Red Cross',
                           'Japanese Red Cross Society',
                           'Iranian Red Crescent',
                           'Department of Refugee Affairs ), United Nations High Commissioner for Refugees',
                           'European Commission Humanitarian Aid and Civil Protection Department ( ECHO ), World Food Programme',
                       

In [ ]:
stanalgo = stanford_entities(fileids=None, corpus=kddcorpus)
pd.DataFrame()

In [ ]:
''''''#stanents
stanents = stanford_entities(fids)
stanents

In [ ]:
#example_id = '- Global - MAA00010 10Nov2015.txt'
#print(kddcorpus.raw(example_id))
#s = 'Bolivia'
#items=re.findall("^.*" + s + ".*$", kddcorpus.raw(example_id), re.MULTILINE)
#items

# POLYGLOT ENTITIES

In [43]:
def polyglot_entities(fileids=None, section = None, corpus=kddcorpus):
    """
    Extract entities from each file using polyglot
    """
    results = defaultdict(lambda: defaultdict(list))
    fileids = fileids or corpus.fileids()


    for fileid in fileids:
        #print(fileid)
        
        if section is not None:
            raw_text = list(sectpull([fileid],section=section))[0][1]
        else:
            raw_text = corpus.raw(fileid)
        raw_text = ''.join(x for x in raw_text if x not in string.printable[-2:])
        text = Text(raw_text)

        for entity in text.entities:
            etext = " ".join(entity)

            if entity.tag == 'Persons_Names':
                key = 'persons'
            elif entity.tag == 'Organization_Names':
                key = 'organizations'
            elif entity.tag == 'Location_Names':
                key = 'locations'
            else:
                key = 'other'

            results[fileid][key].append(etext)

    return results

In [44]:
polyglot_entities(fileids=None, section = None, corpus=kddcorpus)

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.


defaultdict(<function __main__.polyglot_entities.<locals>.<lambda>>,
            {'Kenya MDRKE018 02Oct2015.txt': defaultdict(list,
                         {'other': ['KEN',
                           'Society : Kenya Red Cross',
                           'Ifo',
                           'Crescent Movement',
                           'Committee',
                           'Cross',
                           'Cross',
                           'Red Cross Society',
                           'Crescent',
                           'Hong Kong',
                           'Hong Kong Red Cross',
                           'Government',
                           'Kenya',
                           'Department of Refugee Affairs',
                           'United Nations',
                           'Refugees',
                           'Commission',
                           'Aid',
                           'Civil Protection Department',
                           'Food',
         

In [ ]:
''''''#polyglot_entities(fileids=None, section = None, corpus=kddcorpus)

###  POLYGLOT TABULAR  REPRESENTATION

In [45]:
polyalgo = polyglot_entities(fileids=None, section = None, corpus=kddcorpus)
pd.DataFrame(polyalgo)

Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.


- Global - MAA00001 22Jul2015.txt  \
other  [Health, First, Adolescent, Sanitation, Cross,...   

                       - Global - MAA00006 24Apr2015.txt  \
other  [Global, National Society and Knowledge Develo...   

                       - Global - MAA00010 10Nov2015.txt  \
other  [Crescent, Cross, Red Crescent Societies, Disa...   

                       - Global - MAA00021 02Jun2015.txt  \
other  [World Conference, Sendai, Japan, Geneva, UNIS...   

                       - Global - MAA00028 01May2015.txt  \
other  [Logistics, Global Logistics Service, National...   

                       - Global - MAA00029 21Jun2016.txt  \
other  [Syria, Iraq, Afghanistan, Libya, Ukraine, Yem...   

                       - Global - MAA00040 02Jun2015.txt  \
other  [nternational, of Red, Red Crescent, Managemen...   

                       - Global - MAA00040 10Nov2015.txt  \
other  [Crisis Management Department, Crisis Manageme...   

                       - Global - MAA00040 12May2015.txt  \
other  [Federation of Red, Red Crescent, Management, ...   

                       - Global - MDR00001 01Jun2016.txt  \
other  [Crescent, Cross, Red Crescent Societies, Nati...   

                             ...                          \
other                        ...                           

                         Zimbabwe MDRZW010 26Aug2015.txt  \
other  [Society :, Society : Zimbabwe, Society : Zimb...   

                         Zimbabwe MDRZW011 04Oct2016.txt  \
other  [Jamie LeSueur, Zimbabwe, IFRC, Southern Afric...   

                         Zimbabwe MDRZW011 09May2016.txt  \
other  [Naemi, Southern Africa, Maxwell Phiri, Nation...   

                         Zimbabwe MDRZW011 15Oct2015.txt  \
other  [Naemi, Southern Africa, Maxwell Phiri, Nation...   

                    Zimbabwe MDRZW011 16Sep2015.txt  \
other  [Food, Zimbabwe Red Cross Society, Zimbabwe]   

                         Zimbabwe MDRZW011 18Sep2015.txt  \
other  [Goods, Transport, Cross, British Red Cross, B...   

                         Zimbabwe MDRZW011 24Mar2016.txt  \
other  [EA, Naemi, Southern Africa, Maxwell Phiri, So...   

                         Zimbabwe MDRZW011 27Apr2016.txt  \
other  [Appeal, Zimbabwe Red Cross Society, South, Zi...   

                         Zimbabwe MDRZW011 29Sep2015.txt  \
other  [Naemi, Southern Africa, Maxwell Phiri, Zimbab...   

                                        table_report.txt  
other  [Philippines, Philippines, Typhoon Nock, Phili...  

[1 rows x 1253 columns]

In [ ]:
#all_kddcorpus = polyglot_entities(fileids=None, section = None, corpus=kddcorpus)

# NLTK ENTITIES

In [46]:
def nltk_entities(fileids=None, section = None,corpus=kddcorpus):
    """
    Extract entities using the NLTK named entity chunker.
    """
    results = defaultdict(lambda: defaultdict(list))
    fileids = fileids or corpus.fileids()

    for fileid in fileids:
        if section is not None:
            text = nltk.pos_tag(nltk.word_tokenize(list(sectpull([fileid],section=section))[0][1]))
        else:
            text = nltk.pos_tag(corpus.words(fileid))



        for entity in nltk.ne_chunk(text):
            if isinstance(entity, nltk.tree.Tree):
                etext = " ".join([word for word, tag in entity.leaves()])
                label = entity.label()
            else:
                continue

            if label == 'PERSON':
                key = 'persons'
            elif label == 'ORGANIZATION':
                key = 'organizations'
            elif label == 'LOCATION':
                key = 'locations'
            elif label == 'GPE':
                key = 'other'
            else:
                key = None

            if key:
                results[fileid][key].append(etext)

    return results

In [47]:
nltk_entities(fileids=None, section = None,corpus=kddcorpus)

defaultdict(<function __main__.nltk_entities.<locals>.<lambda>>,
            {'Kenya MDRKE018 02Oct2015.txt': defaultdict(list,
                         {'organizations': ['MDRKE018',
                           'OT',
                           'KEN Date',
                           'Host National Society',
                           'International Committee',
                           'Red Cross',
                           'Department',
                           'United Nations',
                           'Refugees',
                           'European Commission Humanitarian Aid',
                           'ECHO',
                           'CHF',
                           'CHF',
                           'DREF',
                           'Federations',
                           'Emergency Appeal',
                           'CHF'],
                          'other': ['Issue',
                           'Norwegian',
                           'British',
                     

## NLTK ENTITIES TABULAR  REPRESENTATION

In [48]:
nltkalgo = nltk_entities(fileids=None, section = None,corpus=kddcorpus)
pd.DataFrame(nltkalgo)

- Global - MAA00001 22Jul2015.txt  \
locations                                                    NaN   
organizations  [Global Health Report Health, Contents, CBHFA,...   
other           [Disease, Maternal, Neonatal, Child, Sanitation]   
persons               [Annual, Annexes Annex, Health, First Aid]   

                               - Global - MAA00006 24Apr2015.txt  \
locations                                                    NaN   
organizations  [Global, Difference, National Society, NSKD, N...   
other                                     [Geneva, Long, Geneva]   
persons        [Knowledge Development Division, Term Planning...   

                               - Global - MAA00010 10Nov2015.txt  \
locations                                                    NaN   
organizations  [Overview Statistics, DREF, CHF Total, DREF, D...   
other                                        [Bolivia, Bolivian]   
persons        [Start, Red Cross Red Crescent, Emergency Fund...   

                               - Global - MAA00021 02Jun2015.txt  \
locations                                                    NaN   
organizations  [DRR, HFA2, DRR, WCDRR, WCDRR, HFA2, UNISDR, W...   
other                    [Sendai, Japan, Geneva, Cali, Colombia]   
persons                    [Billion Coalition, Climate, Climate]   

                               - Global - MAA00028 01May2015.txt  \
locations                                                    NaN   
organizations  [IFRC Global Logistics Service, GLS, IFRC, Nat...   
other          [Geneva, Panama, Dubai, Las Palmas, Ebola, Ira...   
persons          [Overview, Kuala Lumpur, Nairobi, Guinea, Arab]   

                               - Global - MAA00029 21Jun2016.txt  \
locations                  [West Africa, West Africa, Caribbean]   
organizations  [oPt, Ebola Virus Disease, EVD, Sahel, Horn, R...   
other          [Iraq, Afghanistan, Libya, Palestinian, Yemen,...   
persons        [Latin America, Global Health, Jaime Sepulveda...   

                               - Global - MAA00040 02Jun2015.txt  \
locations                                                    NaN   
organizations  [Red Cross, Red Crescent, MAA00040, DCMs, DCM,...   
other                                                        NaN   
persons        [Crisis Management, Rules, Disaster Relief, Gl...   

                               - Global - MAA00040 10Nov2015.txt  \
locations                                                    NaN   
organizations  [DEVELOPMENT, UPDATE, INTERVENTION, DCM, CHF, ...   
other                                                        NaN   
persons        [Disaster, Crisis Management Department, Globa...   

                               - Global - MAA00040 12May2015.txt  \
locations                                                    NaN   
organizations  [International Federation, Red Cross, Red Cres...   
other                                                        NaN   
persons        [Crisis Management, Crisis Management, Disaste...   

                               - Global - MDR00001 01Jun2016.txt  \
locations                                                    NaN   
organizations  [Overview Statistics, DREF, CHF Total, DREF, D...   
other                                                        NaN   
persons        [Start, Red Cross Red Crescent, Disaster Relie...   

                                     ...                          \
locations                            ...                           
organizations                        ...                           
other                                ...                           
persons                              ...                           

                                 Zimbabwe MDRZW010 26Aug2015.txt  \
locations                                                    NaN   
organizations  [MDRZW010, GLIDE, ZWE Date, Host National Soci...   
other          [DREF, Issue, Norwegian, Mashonaland Central, ...   
persons 

# Sample test for precision and recall


In [54]:
#this testing file has been choosen randomly,and We retrieved personal names from it.
kddcorpus.fileids()[28]

'Africa regional office MDR60002 03Nov2015.txt'

In [55]:
# sample corpus path
fids =['/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt']

## We extracted  manually Personal names from 'Africa regional office MDR60002 03Nov2015.txt'   then  We  want to compare them to Personal names from NLTK, STANFORD and POLYGLOT 

In [56]:
'''stanford entities for person'''

def nltk_entities_test(fileids=None, section = None,corpus=kddcorpus):
    """
    Extract entities using the NLTK named entity chunker.
    """
    results = defaultdict(lambda: defaultdict(list))
    fileids = fileids or corpus.fileids()

    for fileid in fileids:
        if section is not None:
            text = nltk.pos_tag(nltk.word_tokenize(list(sectpull([fileid],section=section))[0][1]))
        else:
            text = nltk.pos_tag(corpus.words(fileid))
            
            
        for entity in nltk.ne_chunk(text):
            if isinstance(entity, nltk.tree.Tree):
                etext = " ".join([word for word, tag in entity.leaves()])
                label = entity.label()
            else:
                continue

            if label == 'PERSON':
                key = 'persons'
            
            if key:
                results[fileid][key].append(etext)

    return results

In [117]:
#print(nltk_entities_test(fileids=fids, section = None,corpus=kddcorpus))

In [121]:
fids = ['/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt']

In [119]:
#example_filename = '/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt'
#nltkents = nltk_entities_test(fids, section = None,corpus=kddcorpus)
#nltkents['/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt']['persons']
#nltk_persons = {file: D['persons'] for file, D in nltkents.items()}
#nltk_persons[example_filename]

In [120]:
pd.Series(nltkents)

/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt    {'persons': ['Mamadou Basilah', 'Klalantou', '...
dtype: object

In [102]:
#pd.Series(nltkents[fids[0]]['persons']).T

In [87]:



#nltkents = nltk_entities_test(fids, section = None,corpus=kddcorpus)
#nltkents['/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt']['persons']
#nltk_persons = {file: D['persons'] for file, D in nltkents.items()}
#nltk_persons[example_filename]

In [106]:
#stanford_entities_test(fileids=None, corpus=kddcorpus)

In [128]:
fids= ['/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt']
stanents = stanford_entities_test(fids)
stan_persons = {file: D['persons'] for file, D in stanents.items()}
print(stan_persons[fids[0]])
len(stan_persons[fids[0]])

['Mamadou Basilah', 'Forecariah', 'Guinea', 'Ebola', 'Tommy Trenchard  IFRC Emergency', '2014', 'NGA', 'November 2015', 'Norbert Allale', 'Norbert Allale', 'Head of Ebola Regional Operations', 'Months Update Timeframe', 'August 2014 20 August 2015', 'August 2014', 'December 2015', '85 %', 'August 2014', 'January 2015', 'December 2015', 'Million Red Cross Red Crescent Movement', 'Liberian National Red Cross Society', 'Sierra Leone Red Cross Society', 'Danish Red Cross', 'French Red Cross', 'German Red Cross', 'Netherlands Red Cross', 'Spanish Red Cross', 'Swiss Red Cross', 'ICRC', 'UNICEF', 'CDC', 'Action Contre la Faim', 'Institut Pasteur Dakar', 'Catholic Relief Services', 'CAFOD', 'Caritas', 'Samaritans Purse']


37

In [124]:
#stan_persons = {file: D['persons'] for file, D in nltkents.items()}
#print(stan_persons[fids[0]])
#len(stan_persons[fids[0]])

In [103]:
#stanford_entities_test(fileids=fids, corpus=kddcorpus)

###  Polyglot testing

In [125]:
def polyglot_entities_test(fileids=None, section = None, corpus=kddcorpus):
    """
    Extract entities from each file using polyglot
    """
    results = defaultdict(lambda: defaultdict(list))
    fileids = fileids or corpus.fileids()


    for fileid in fileids:
        #print(fileid)
        
        if section is not None:
            raw_text = list(sectpull([fileid],section=section))[0][1]
        else:
            raw_text = corpus.raw(fileid)
        raw_text = ''.join(x for x in raw_text if x not in string.printable[-2:])
        text = Text(raw_text)

        for entity in text.entities:
            etext = " ".join(entity)

            if entity.tag == 'Persons_Names':
                key = 'persons'
        
                results[fileid][key].append(etext)

    return results

In [127]:
#polyglot_entities_test(fileids=fids, section = None, corpus=kddcorpus)[2]

In [134]:
#polyents = polyglot_entities(fids)
#polyents 

polyents = polyglot_entities_test(fids)
poly_persons = {file: D['persons'] for file, D in polyents.items()}
poly_persons
#print(poly_persons[fids[0]])
#len(poly_persons[fids[0]])



{}

In [69]:
#fids = ['/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt']

In [70]:
#nltkents

In [71]:
# Polyglot Entities
polyents = polyglot_entities(fids)
polyents

defaultdict(<function __main__.polyglot_entities.<locals>.<lambda>>,
            {'/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt': defaultdict(list,
                         {'other': ['Mamadou Basilah',
                           'Klalantou',
                           'Forecariah',
                           'Guinea',
                           'Tommy Trenchard',
                           'SEN',
                           'Norbert Allale',
                           'Norbert Allale',
                           'Ebola',
                           'Operations',
                           'Crescent Movement',
                           'Guinea',
                           'Cross',
                           'Liberian',
                           'Red Cross Society',
                           'Sierra',
                           'Sierra Leone',
                           'Sierra Leone Red Cross Society',
     

In [135]:
# Stanford Entities
#fids = ['/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt']
#jar  = os.path.join(root, 'stanford-ner-2014-01-04.jar')
#stanents = stanford_entities_test(fids, corpus=kddcorpus)
#stanents

In [136]:
#list_keys = [stanents[k] for k in stanents]; 
#list_keys
#pd.Series(stanents['persons'])

In [140]:
def nltk_entities_test(fileids=None, section = None,corpus=kddcorpus):
    """
    Extract entities using the NLTK named entity chunker.
    """
    results = defaultdict(lambda: defaultdict(list))
    fileids = fileids or corpus.fileids()

    for fileid in fileids:
        if section is not None:
            text = nltk.pos_tag(nltk.word_tokenize(list(sectpull([fileid],section=section))[0][1]))
        else:
            text = nltk.pos_tag(corpus.words(fileid))



        for entity in nltk.ne_chunk(text):
            if isinstance(entity, nltk.tree.Tree):
                etext = " ".join([word for word, tag in entity.leaves()])
                label = entity.label()
            else:
                continue

            if label == 'PERSON':
                key = 'persons'
            else:
                key = None

            if key:
                results[fileid][key].append(etext)

    return results

In [159]:
polyents = nltk_entities_test(fileids=fids, section = None,corpus=kddcorpus)
polyents

defaultdict(<function __main__.nltk_entities_test.<locals>.<lambda>>,
            {'/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt': defaultdict(list,
                         {'persons': ['Mamadou Basilah',
                           'Tommy Trenchard',
                           'Norbert Allale Point',
                           'Norbert Allale',
                           'Ebola Regional Operations',
                           'Appeal',
                           'Guinea Red Cross',
                           'Liberian National Red Cross Society',
                           'Sierra Leone Red Cross Society',
                           'Danish Red Cross',
                           'German Red Cross',
                           'Netherlands Red Cross',
                           'Swiss Red Cross',
                           'Action Contre',
                           'Institut Pasteur Dakar',
                  

In [148]:
fids= ['/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt']
polyents = polyglot_entities_test(fids)

poly_persons = {file: D['persons'] for file, D in polyents.items()}
poly_persons
#print(poly_persons[fids[0]])
#len(poly_persons[fids[0]])

{}

In [149]:
#stanford_entities(['/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt'], corpus=kddcorpus)

In [150]:

#fids_details = json.load(open('./home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/fids.json'))

In [151]:
fids = ['/home/alice/Documents/Project/info_extraction/scraped_data/initial_lines_txt/Africa regional office MDR60002 03Nov2015.txt']
stanents = stanford_entities_test(fids)
stanents[fids[0]]

defaultdict(list,
            {'persons': ['Mamadou Basilah',
              'Forecariah',
              'Guinea',
              'Ebola',
              'Tommy Trenchard  IFRC Emergency',
              '2014',
              'NGA',
              'November 2015',
              'Norbert Allale',
              'Norbert Allale',
              'Head of Ebola Regional Operations',
              'Months Update Timeframe',
              'August 2014 20 August 2015',
              'August 2014',
              'December 2015',
              '85 %',
              'August 2014',
              'January 2015',
              'December 2015',
              'Million Red Cross Red Crescent Movement',
              'Liberian National Red Cross Society',
              'Sierra Leone Red Cross Society',
              'Danish Red Cross',
              'French Red Cross',
              'German Red Cross',
              'Netherlands Red Cross',
              'Spanish Red Cross',
              'Swiss Red Cross',
 

## Json file : I created manually a Json file contains person names from forst 25 lines of  a sample report" " in order to check accuracy,precision and recall.

In [152]:
manual_file = open('manual_file.json', 'r')
conn_string = json.load(manual_file)
conn_string

{'BothNames': {'1': 'Mamadou Basilah',
  '2': 'Tommy Trenchard',
  '3': 'Norbert Allale'},
 'SingleName': {'1': 'Mamadou',
  '2': 'Basilah',
  '3': 'Tommy',
  '4': 'Trenchard',
  '5': 'Norbert',
  '6': 'Allale'}}

In [153]:
# ordered
manual = json.load(open('manual_file.json'))


In [156]:
#stanents(fids)

In [155]:
df1 = pd.Series(polyents[fids[0]]['persons'], index=None,
dtype=None, name='Polyglot NERC Authors', copy=False, fastpath=False)

df2=pd.Series([re.sub('\*',"",l) for l in stanents[fids[0]]['persons']],
index=None, dtype=None, name='Stanford NERC Authors', copy=False, fastpath=False)

df3=pd.Series([re.sub('\*',"",l) for l in nltkents[fids[0]]['persons']],
index=None, dtype=None, name='NLTKStandard NERC Authors', copy=False, fastpath=False)

df4 = pd.Series(manual['BothNames'], index=None,
dtype=None, name='Hand-labeled True BothNames', copy=False, fastpath=False)

met = pd.concat([df4,df3,df2,df1], axis=1).fillna('')
met

/home/alice/.local/lib/python3.4/site-packages/pandas/indexes/api.py:71: RuntimeWarning: unorderable types: int() > str(), sort order is undefined for incomparable objects
  result = result.union(other)


Hand-labeled True BothNames            NLTKStandard NERC Authors  \
1              Mamadou Basilah                                        
2              Tommy Trenchard                                        
3               Norbert Allale                                        
0                                                   Mamadou Basilah   
1                                                         Klalantou   
2                                                        Forecariah   
3                                                            Guinea   
4                                                             Ebola   
5                                                   Tommy Trenchard   
6                                                    MDR60002 Glide   
7                                                                EP   
8                                                               SLE   
9                                                               LBR   
10                                                            Issue   
11                                             Norbert Allale Point   
12                                                   Norbert Allale   
13                                        Ebola Regional Operations   
14                                                           Update   
15                                                           Appeal   
16                                                           Appeal   
17                                                              CHF   
18                                                              CHF   
19                                                 Guinea Red Cross   
20                              Liberian National Red Cross Society   
21                                   Sierra Leone Red Cross Society   
22                                                 Danish Red Cross   
23                                                           French   
24                                                 German Red Cross   
25                                            Netherlands Red Cross   
26                                                          Spanish   
27                                                  Swiss Red Cross   
28                                                             ICRC   
29                                                           Health   
30                                                              WHO   
31                                                           UNICEF   
32                                                              CDC   
33                                                         Medecins   
34                                                         Children   
35                                                    Action Contre   
36                                           Institut Pasteur Dakar   
37                                         Catholic Relief Services   
38                                                Concern Worldwide   
39                                                     World Vision   
40                                                             CARE   
41                                                            CAFOD   
42                                                          Caritas   
43                                                             Plan   
44                                                 Samaritans Purse   
45                                                             Semi   

                      Stanford NERC Authors Polyglot NERC Authors  
1                                                                  
2                                                                  
3                                                                  
0                           Mamadou Basilah                        
1                                Forecariah                        
2                                    Guinea 